# 필요한 패키지들부터 설치!!

In [1]:
!pip install beautifulsoup4
!pip install requests
!pip install textblob
!pip install nltk

In [2]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [0]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
from textblob.classifiers import NaiveBayesClassifier

In [0]:
def is_digit(str):
  try:
    tmp = float(str)
    return True
  except ValueError:
    return False

In [0]:
def score_transfer(score):

  score_list = score.split("/")
  score = 0

  if is_digit(score_list[0]) == True:
    if len(score_list) == 2:
      score = float(score_list[0])/float(score_list[1])
  else:

    if score_list[0][0] == "A":
      score = 0.8
    elif score_list[0][0] == "B":
      score = 0.6
    elif score_list[0][0] == "C":
      score = 0.4
    elif score_list[0][0] == "D":
      score = 0.2

    if len(score_list[0]) == 2:
      if score_list[0][1] == "+":
        score = score + 0.1
      elif score_list[0][1] == "-":
        score = score - 0.1

  if score > 0.5:
    score = "pos"
  elif score <= 0.5:
    score = "neg"

  transformed_score = score
  return transformed_score

In [0]:
movie_name_list = ["terminator_dark_fate","joker_2019","maleficent_mistress_of_evil","harriet", "the_addams_family_2019","zombieland_double_tap"]

In [0]:
review_table = []

for movie_name in movie_name_list:
  url = requests.get("https://www.rottentomatoes.com/m/" + movie_name + "/reviews?type=&sort=&page=1")
  soup = BeautifulSoup(url.text, "html.parser")
  Totalpagenum = soup.find("span", attrs={"class":"pageInfo"})
  Totalpagenum = Totalpagenum.text.split(" ")[3]

  for num in range(1, int(Totalpagenum)):
    url = requests.get("https://www.rottentomatoes.com/m/" + movie_name + "/reviews?type=&sort=&page="+str(num))
    soup = BeautifulSoup(url.text, "html.parser")

    all_review = soup.findAll("div", attrs={"class":"row review_table_row"})
    for line in all_review:
      review = line.find("div", attrs={"class":"the_review"}).get_text().strip()
      review_point = line.find("div", attrs={"class":"small subtle review-link"}).get_text()
      review_point = review_point.split(":")
      if len(review_point) > 1:
        score = score_transfer(review_point[1].strip())
      
      review_table.append([review, score])

In [20]:
import random

pos_num = 0
neg_num = 0
positive_list = []
negative_list = []
for review in review_table:
    if review[1] == "pos":
      pos_num += 1
      positive_list.append(review)
    elif review[1] == "neg":
      neg_num +=1 
      negative_list.append(review)
  
positivi2_list = random.sample(positive_list, 486)
print (pos_num, neg_num)
print (len(positivi2_list))
print (len(negative_list))

974 486
486
486


In [26]:
train_size = len(positivi2_list)*0.8

pos_train_set = positivi2_list[:int(train_size)]
pos_test_set = positivi2_list[int(train_size):]
neg_train_set = negative_list[:int(train_size)]
neg_test_set = negative_list[int(train_size):]

print (len(pos_train_set), len(neg_train_set), len(pos_test_set), len(neg_test_set))

train_set = pos_train_set + neg_train_set
test_set = pos_test_set + neg_test_set

388 388 98 98


In [0]:
cl = NaiveBayesClassifier(train_set)

In [28]:
cl.accuracy(test_set)

0.46938775510204084

In [30]:
cl.show_informative_features(10)

Most Informative Features
      contains(Mistress) = True              neg : pos    =      7.2 : 1.0
          contains(Evil) = True              neg : pos    =      7.0 : 1.0
         contains(right) = True              pos : neg    =      5.8 : 1.0
        contains(Addams) = True              pos : neg    =      5.0 : 1.0
    contains(Maleficent) = True              neg : pos    =      4.9 : 1.0
     contains(brilliant) = True              pos : neg    =      4.3 : 1.0
          contains(thin) = True              neg : pos    =      4.3 : 1.0
         contains(wants) = True              neg : pos    =      4.3 : 1.0
  contains(conventional) = True              pos : neg    =      4.3 : 1.0
       contains(sequels) = True              neg : pos    =      4.3 : 1.0
